# Dataset Analysis

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from openai import OpenAI

## Correctness
$\textit{How well the generated tests reflect their objective?}$

### Manual Check

* Sampling for the manual check. By default, 10 tests are sampled for each of 30 biases, thus constituting 1% of the dataset

In [2]:
def check_manually(path_to_dataset: str, biases: list[str], n: int = 10, seed: int = 0) -> int:
    """
    This function samples n corresponding tests from the dataset and initiates a manual check by the user.
    
    Args:
        path_to_dataset (str): the path to the dataset
        biases (list[str]): the biases to sample tests from
        n (int): the number of tests to sample
        seed (int): the seed for the random sampling
    
    Returns:
        int: 0 if the manual check was completed successfully
    """
    dataset = pd.read_csv(path_to_dataset)
    sample = dataset[dataset['bias'].isin(biases)].sample(n=n, random_state=seed)
    for bias in biases:
        print(f'Start of the review for: {bias}. Answer 1 if the test is correct, 0 if it is not.')
        for i, row in sample.iterrows():
            correctness = None
            print('-----------------------------------')
            print(f'SCENARIO:\n{row["scenario"]}\n')
            print(f'CONTROL:\n{row["control"]}')
            print(f'TREATMENT:\n{row["treatment"]}')
            while correctness not in ['1', '0']:
                correctness = input('Correct? (1 - yes/0 - no): ')  
            sample.loc[i, 'correct'] = int(correctness)
            
    sample.to_csv('manual_check.csv', index=False)
    
    return 0

* Statistics of the manual check

In [4]:
# TODO

### LLM-as-a-judge 
[Original research](https://arxiv.org/abs/2306.05685) and a [helpful link](https://huggingface.co/learn/cookbook/en/llm_judge).

TBD

## Diversity
$\textit{How diverse are the generated tests?}$

### General statistics

### String-based similarity metrics

### Embedding-based tests

* toxicity analysis using [Detoxify](https://github.com/unitaryai/detoxify?tab=readme-ov-file)

In [12]:
from detoxify import Detoxify

def analyse_toxicity(dataset: pd.DataFrame) -> pd.DataFrame:
    """
    This function calculates the Detoxify scores for each test in the dataset.
    
    Args:
        dataset (pd.DataFrame): the dataset
    
    Returns:
        pd.DataFrame: the dataset with the Detoxify scores
    """
    for bias in dataset['bias'].unique():
        print(f'Analyzing bias: {bias}')
        # if the test has no control, we skip it
        try:
            control_test = [text.replace("\n", " ") for text in dataset[dataset['bias'] == bias]['control'].tolist()]
            control_scores = Detoxify('original').predict(control_test)
            for key, value in control_scores.items():
                dataset.loc[dataset['bias'] == bias, f'control_{key}'] = value
        except Exception:
            print(f'No control scores for bias: {bias}')
            control_scores = {}
            continue
        # calculate the treatment scores
        treatment_test = [text.replace("\n", " ") for text in dataset[dataset['bias'] == bias]['treatment'].tolist()]
        treatment_scores = Detoxify('original').predict(treatment_test)
        for key, value in treatment_scores.items():
            dataset.loc[dataset['bias'] == bias, f'treatment_{key}'] = value
        # calculate the average scores for the test if both control and treatment are present, otherwise use the treatment scores
        for key in treatment_scores.keys():
            if key in control_scores.keys():
                dataset.loc[dataset['bias'] == bias, f'{key}'] = (dataset.loc[dataset['bias'] == bias, f'treatment_{key}'] + dataset.loc[dataset['bias'] == bias, f'control_{key}']) / 2
            else:
                dataset.loc[dataset['bias'] == bias, f'{key}'] = dataset[dataset['bias'] == bias][f'treatment_{key}']
        
        dataset.drop(columns=[f'control_{key}' for key in control_scores.keys()] + [f'treatment_{key}' for key in treatment_scores.keys()], inplace=True)
        
    print(f'Finished the analysis.')
    
    return dataset


def visualise_toxicity(dataset: pd.DataFrame) -> None:
    """
    This function produces a heatmap visualisation for the toxicity scores in the dataset.
    
    Args:
        dataset (pd.DataFrame): the dataset with the Detoxify scores
    """
    grouped_traits = dataset.groupby('bias')[['toxicity', 'severe_toxicity', 'obscene', 'threat', 'insult', 'identity_attack']].max()
    grouped_traits.sort_index(inplace=True)
    plt.figure(figsize = (20,10), dpi=1200)
    ax = sns.heatmap(grouped_traits.rename(columns={'toxicity': 'Toxicity',
                                                    'severe_toxicity': 'Severe Toxicity',
                                                    'obscene': 'Obscene',
                                                    'threat': 'Threat',
                                                    'insult': 'Insult',
                                                    'identity_attack': 'Identity Attack'}).T.rename(columns={'FundamentalAttributionError': 'FAE'}), 
                     xticklabels=True, 
                     yticklabels=True, 
                     cmap=sns.diverging_palette(230, 20, as_cmap=True), 
                     square=True, 
                     cbar_kws={"shrink": .35}, 
                     linewidths=.5)
    plt.xticks(rotation=70)
    ax.set_ylabel(''), ax.set_xlabel('')
    ax.set_title('Average Detoxify Scores for Test Cases by Bias')
    plt.show()
    
    return None

In [13]:
# This is a pseudo implementation to display the visualisation. 
# The actual visualisation will be done after the dataset is composed.

from script import get_all_biases

all_biases = get_all_biases()
toxicity_dict = {}
toxicity_dict.update({'bias': all_biases})
for param in ['toxicity', 'severe_toxicity', 'obscene', 'threat', 'insult', 'identity_attack']:
    toxicity_dict[param] = np.random.gamma(1, 0.01, len(all_biases))
foo_dataset = pd.DataFrame(toxicity_dict)

visualise_toxicity(foo_dataset)


* Embedding visualisation

In [20]:
# OpenAI embedding models: one of ['text-embedding-3-small', 'text-embedding-3-large', 'text-embedding-ada-002']
from dotenv import load_dotenv
from sklearn.manifold import TSNE

load_dotenv()

MODEL = 'text-embedding-3-small'
EMBEDDING_DIM = 1536
client = OpenAI()

def get_embedding(text, model="text-embedding-3-small"):
    text = text.replace("\n", " ")
    return client.embeddings.create(input = [text], model=model).data[0].embedding

def collect_embeddings(dataset: pd.DataFrame) -> tuple[np.ndarray, list[str]]:
    """
    This function collects the embeddings for the tests in the dataset.
    
    Args:
        dataset (pd.DataFrame): the dataset
    
    Returns:
        tuple[np.ndarray, list[str]]: the embeddings and the respective biases
        
    """
    embeddings = np.empty((0, EMBEDDING_DIM))
    biases = []
    
    for bias in dataset['bias'].unique():
        print(f'Embedding bias: {bias}')
        # if the test has no control, we skip it
        try:
            control_embeddings = np.array([get_embedding(i, model=MODEL) for i in dataset[dataset['bias'] == bias]['control'].to_list()])
        except Exception:
            print(f'No control embeddings for bias: {bias}')
            control_embeddings = None
            continue
        # calculate the treatment embeddings
        treatment_embeddings = np.array([get_embedding(i, model=MODEL) for i in dataset[dataset['bias'] == bias]['treatment'].to_list()])
        # calculate the average embedding for the test if both control and treatment are present, otherwise use the treatment one
        if control_embeddings is not None:
            embeddings = np.concatenate((embeddings, (control_embeddings + treatment_embeddings) / 2))
        else:
            embeddings = np.concatenate((embeddings, treatment_embeddings))
        biases += [bias] * len(dataset[dataset['bias'] == bias])
        
    print(f'Finished the embedding procedure.')
    
    return embeddings, biases


def visualise_embeddings(embeddings: np.array, biases: list[str], method: str = 't-SNE', random_state: int = 0) -> None:
    """
    This function visualises the embeddings using a method of choice.
    
    Args:
        embeddings (np.array): the embeddings
        biases (list[str]): the respective biases
        method (str): the method for the visualisation
        random_state (int): the random state for the visualisation
    """
    if method == 't-SNE':
        embeddings_2d = TSNE(n_components=2, learning_rate='auto', init='random', perplexity=3, random_state=random_state).fit_transform(embeddings)
    elif method == 'UMAP':
        pass
    
    visual_df = pd.DataFrame()
    visual_df['X'], visual_df['Y'] = embeddings_2d[:, 0], embeddings_2d[:, 1]
    visual_df['bias'] = biases 

    #plt.rcParams['figure.dpi'] = 450
    plt.figure(figsize = (16, 10), dpi=1200)
    markers = ['o', 's', 'D', 'p', 'X', 'P']
    ax = sns.scatterplot(x='X', y='Y', hue='bias', linewidth=0, data=visual_df, s=30, palette=sns.diverging_palette(230, 20, n=28, as_cmap=False), style="bias", markers=markers)
    sns.move_legend(
    ax, "right",
    bbox_to_anchor=(1.22, 0.6), ncol=1, title=None, frameon=False, fontsize=10
    )
    ax.set_ylabel(''), ax.set_xlabel('')
    plt.title('Two dimensional t-SNE of the test cases')
    plt.show()

In [114]:
dataset = pd.read_csv('dataset.csv')
embeddings, biases = collect_embeddings(dataset)

In [21]:
# Another pseudo implementation to display the visualisation.

from script import get_all_biases

all_biases = get_all_biases()
biases = []
for bias in all_biases:
    biases += [bias] * 10
embeddings = np.random.rand(280, 1536)

visualise_embeddings(embeddings, biases)

/var/folders/g0/m852bq5j7gd84y0trm3pm2yr0000gn/T/ipykernel_27391/1526021127.py:74: UserWarning: 
The markers list has fewer values (6) than needed (28) and will cycle, which may produce an uninterpretable plot.
  ax = sns.scatterplot(x='X', y='Y', hue='bias', linewidth=0, data=visual_df, s=30, palette=sns.diverging_palette(230, 20, n=28, as_cmap=False), style="bias", markers=markers)
